# Handgeschriebene Ziffern erkennen
### Anwendung eines neuronalen Netzes

Das hier vorliegende Programm stellt eine Implementierung eines neuronalen Netzes dar. Speziell wird es hier angewandt, um handgeschriebene Ziffern zu erkennen. Es liegen Datensätze mit 60.000 handgeschriebenen Ziffern vor, dargestellt als 28x28-Pixel-Bilder. Diese Daten werden in mehreren Durchläufen zum Trainieren des neuronalene Netzes verwendet.

Weitere 10.000 entsprechende Datensätze dienen zum Testen des neuronalen Netzes. Es wird eine Erkennungsrate von über 97 % erzielt.

Das folgende Programm enthält zunächst Definitionen von Funktionen *readInput* und *prepareInput*, mit denen die Eingabedaten eingelesen und aufbereitet werden. Dann kommt die Definition der Aktivierungsfunktion *sigma*. Die eigentlichen Funktionen des neuronalen Netzes, nämlich *propagate*, *backpropagate*, *train* und *test* schließen sich an.

Im Hauptprogramm wird das neuronale Netz zunächst definiert, indem pro Schicht die Anzahl der Neuronen angegeben wird. Hier etwa wird ein neuronales Netz mit drei Schichten definiert, wobei die Eingabeschicht 28 * 28 = 784 Neuronen umfasst, die innere Schicht 200 Neuronen und die Ausgabeschicht 10 Neuronen. Alternativ, hier im Programmtext auskommentiert, wird ein neuronales Netz mit vier Schichten definiert.

Überraschenderweise hat die Initialisierung der Gewichtungsmatrizen erheblichen Einfluss auf die Erkennungsrate des neuronalen Netzes. Hier ist eine Initialisierung gewählt, die normalverteilte Zufallswerte enthält.

Für die im Verlauf der Berechnung erforderlichen Vektoren werden zunächst Platzhalter erzeugt, sodass später per Indizierung darauf zugegriffen werden kann (zum Beispiel muss e[0] vorhanden sein, wenn ihm ein Wert zugewiesen wird).

Es folgt dann das Programmstück zum Trainieren und Testen des neuronalen Netzes. Die 60.000 Trainingsdatensätze werden mehrfach in sogenannten Epochen in das Netz eingegeben, um es zu trainieren. Im Anschluss daran wird mit den 10.000 Testdatensätzen jeweils die erzielte Erkennungsrate bestimmt. 

In [ ]:
import numpy as np

# Daten aus Datei einlesen
def readInput(filename):
    datafile=open(filename, 'r')
    datalist=datafile.readlines()
    datafile.close()
    return datalist

# Daten für die weitere Verwendung aufbereiten
def prepareInput(datalist):
    r=[]
    for z in datalist:
        v=z.split(',')
        x=[int(s) for s in v]
        d=x[0]
        x=[t-128 for t in x[1:]]
        y=[0.1]*10
        y[d]=0.9
        r+=[y+x]
    return r

# Aktivierungsfunktion
def sigma(x):
    return 1.0/(1+np.exp(-x))

# Eingabevektor x durch das neuronale Netz schicken
def propagate(x):
    e[0]=np.array(x).reshape(1,m[0])  # 1 x m[0]-Matrix
    s[0]=sigma(e[0])
    for r in range(1, n):
        e[r]=np.matmul(s[r-1], w[r-1])
        s[r]=sigma(e[r])

# Zielvektor y durch das neuronale Netz zurückverbreiten
# und dabei die Gewichtungen anpassen
def backpropagate(y):
    y=np.array(y).reshape(1, m[n-1])  # 1 x m[n-1]-Matrix
    r=n-1
    f[r]=s[r] - y
    h[r]=f[r]*s[r]*(1-s[r])
    # Fehler zurückpropagieren
    for r in range(n-2, 0, -1):
        f[r]=np.matmul(h[r+1], w[r].T)
        h[r]=f[r]*s[r]*(1-s[r])
    # Gewichte anpassen
    for r in range(n-1, 0, -1):
        w[r-1] -= np.matmul(s[r-1].T, alpha*h[r])

# das neuronale Netz mit den Trainingsdaten trainieren
def train():
    for z in traindata:
        x=z[10:]
        propagate(x)
        y=z[:10]
        backpropagate(y)

# das neuronale Netz mit den Testdaten testen
# und die Erkennungsrate bestimmen
def test():
    cnt=0
    for z in testdata:
        x=z[10:]
        propagate(x)
        y=z[:10]
        p=np.argmax(y)
        q=np.argmax(s[n-1][0])  # [0] weil 1 x m_n-1-Matrix
        if p==q:
            cnt+=1
    return 100.0*cnt/len(testdata)  # Prozent richtig erkannt
       
# Neuronales Netz definieren
# Anzahl der Neuronen pro Schicht
#m=[28*28, 200, 10]
#m=[28*28, 14*14, 7*7, 10]
m=[28*28, 50, 50, 50, 10]
n=len(m)    # Anzahl der Schichten
# Liste mit Gewichtungsmatrizen:
w=[np.random.normal(0.0, pow(m[r-1], -0.5), (m[r-1], m[r])) for r in range(1,n)]
e=[0]*n  # Platzhalter für Eingabevektoren
s=[0]*n  # Platzhalter für Ausgabevektoren
f=[0]*n  # Platzhalter für Fehlervektoren
h=[0]*n  # Platzhalter für Fehlervektoren

print("Eingabedaten einlesen...")
# Trainingsdaten einlesen
traindata=prepareInput(readInput("mnist_train.csv"))
# Testdaten einlesen
testdata=prepareInput(readInput("mnist_test.csv"))

# Mehrere Epochen mit jeweils 60.000 Trainingsdatensätzen und
# anschließendem Test mit 10.000 Testdatensätzen durchlaufen,
# nach und nach die Lernrate verringern
epochs=6
for i in range(epochs):
    print("Epoche %d: Training..." % (i+1), end="  ")
    alpha=0.1*(epochs-i)  # Lernrate nach und nach verringern
    train()
    print("Test...", end="  ")
    p=test()
    print("Erkennung:%6.2f %%" % p)
print("fertig")


Eingabedaten einlesen...
Epoche 1: Training...  Test...  Erkennung: 93.44 %
Epoche 2: Training...  Test...  Erkennung: 94.67 %
Epoche 3: Training...  Test...  Erkennung: 95.38 %
Epoche 4: Training...  Test...  Erkennung: 96.03 %
Epoche 5: Training...  Test...  

Das folgende Programm stellt eine Ziffer aus dem Testdatensatz grafisch auf dem Bildschirm dar. Zuvor muss das obige Programm einmal ausgeführt worden sein, damit der Datensatz *testdata* vorhanden ist.

In [ ]:
import numpy as np
import matplotlib.pyplot
%matplotlib inline

row=testdata[15]
imagearray=np.array(row[10:]).reshape((28,28))
matplotlib.pyplot.imshow(imagearray, cmap='Greys')
